In [ ]:
!pip install catboost

     |████████████████████████████████| 67.3MB 51kB/s 


In [ ]:
import pandas as pd
import numpy as np
import typing as tp
from catboost import CatBoostRegressor, CatBoostClassifier
import matplotlib.pyplot as plt
%matplotlib inline

In [ ]:
from google.colab import files
files.upload()

Saving train.csv to train.csv


{'train.csv': b',Division,Time,home_team,away_team,full_time_home_goals,full_time_away_goals,half_time_home_goals,half_time_away_goals,Referee,home_shots,away_shots,home_shots_on_target,away_shots_on_target,home_fouls,away_fouls,home_corners,away_corners,home_yellow_cards,away_yellow_cards,home_red_cards,away_red_cards,home_coef,draw_coef,away_coef\r\n0,0,,152.0,426.0,0.0,0.0,0.0,0.0,-1,,,,,,,,,,,,,3.6276895846009176,3.577721408504487,2.1985997482429807\r\n1,0,,216.0,341.0,2.0,2.0,0.0,1.0,-1,,,,,,,,,,,,,1.608321224921183,4.251999238385378,6.533804976242305\r\n2,0,,223.0,119.0,2.0,2.0,2.0,0.0,-1,,,,,,,,,,,,,2.166811124586162,3.4865960822886413,3.8214668924519573\r\n3,0,,68.0,137.0,2.0,1.0,0.0,1.0,-1,,,,,,,,,,,,,2.259243921392639,3.59240137050271,3.4601033030337716\r\n4,1,,425.0,225.0,2.0,2.0,1.0,0.0,-1,13.0,11.0,5.0,7.0,18.0,15.0,4.0,10.0,3.0,4.0,1.0,0.0,2.4242779307516553,3.4141914191419143,3.2828763645595327\r\n5,1,,393.0,300.0,0.0,0.0,0.0,0.0,-1,6.0,6.0,1.0,2.0,9.0,13.0,6.0,8.0,1.0,0

In [ ]:
stat_df = pd.read_csv('train.csv')
stat_df

Unnamed: 0  Division  Time  ...  home_coef  draw_coef  away_coef
0               0         0   NaN  ...   3.627690   3.577721   2.198600
1               1         0   NaN  ...   1.608321   4.251999   6.533805
2               2         0   NaN  ...   2.166811   3.486596   3.821467
3               3         0   NaN  ...   2.259244   3.592401   3.460103
4               4         1   NaN  ...   2.424278   3.414191   3.282876
...           ...       ...   ...  ...        ...        ...        ...
39987       39995        15   NaN  ...   2.102645   3.404282   4.155226
39988       39996        15   NaN  ...   1.340170   5.956310  10.423542
39989       39997        15   NaN  ...   1.963689   3.506588   4.638715
39990       39998        13   NaN  ...   4.050577   3.852988   1.985771
39991       39999         6   NaN  ...   1.732761   3.924194   5.616183

[39992 rows x 25 columns]

In [ ]:
stat_df = stat_df.rename(columns={"full_time_home_goals": "home_full_time_goals",
                                  "full_time_away_goals": "away_full_time_goals",
                                  "half_time_home_goals": "home_half_time_goals",
                                  "half_time_away_goals": "away_half_time_goals"})

In [ ]:
stat_df

Unnamed: 0  Division  Time  ...  home_coef  draw_coef  away_coef
0               0         0   NaN  ...   3.627690   3.577721   2.198600
1               1         0   NaN  ...   1.608321   4.251999   6.533805
2               2         0   NaN  ...   2.166811   3.486596   3.821467
3               3         0   NaN  ...   2.259244   3.592401   3.460103
4               4         1   NaN  ...   2.424278   3.414191   3.282876
...           ...       ...   ...  ...        ...        ...        ...
39987       39995        15   NaN  ...   2.102645   3.404282   4.155226
39988       39996        15   NaN  ...   1.340170   5.956310  10.423542
39989       39997        15   NaN  ...   1.963689   3.506588   4.638715
39990       39998        13   NaN  ...   4.050577   3.852988   1.985771
39991       39999         6   NaN  ...   1.732761   3.924194   5.616183

[39992 rows x 25 columns]

In [ ]:
stat_df['Referee'] = stat_df['Referee'].replace(-1, np.nan)

In [ ]:
stat_df

Unnamed: 0  Division  Time  ...  home_coef  draw_coef  away_coef
0               0         0   NaN  ...   3.627690   3.577721   2.198600
1               1         0   NaN  ...   1.608321   4.251999   6.533805
2               2         0   NaN  ...   2.166811   3.486596   3.821467
3               3         0   NaN  ...   2.259244   3.592401   3.460103
4               4         1   NaN  ...   2.424278   3.414191   3.282876
...           ...       ...   ...  ...        ...        ...        ...
39987       39995        15   NaN  ...   2.102645   3.404282   4.155226
39988       39996        15   NaN  ...   1.340170   5.956310  10.423542
39989       39997        15   NaN  ...   1.963689   3.506588   4.638715
39990       39998        13   NaN  ...   4.050577   3.852988   1.985771
39991       39999         6   NaN  ...   1.732761   3.924194   5.616183

[39992 rows x 25 columns]

In [ ]:
stat_df.describe()

Unnamed: 0      Division  ...     draw_coef     away_coef
count  39992.000000  39992.000000  ...  39992.000000  39992.000000
mean   19999.027731      9.760827  ...      3.872743      4.490756
std    11546.629417      5.269941  ...      1.132322      3.629462
min        0.000000      0.000000  ...      2.524868      1.102549
25%     9999.750000      6.000000  ...      3.389876      2.759872
50%    19998.500000     10.000000  ...      3.562471      3.568531
75%    29998.250000     14.000000  ...      3.888294      4.839698
max    39999.000000     19.000000  ...     28.959884     66.225294

[8 rows x 25 columns]

In [ ]:
print("Number of unique teams:", stat_df["home_team"].nunique())

Number of unique teams: 464


In [ ]:
columns_known_before_match = ['Division', 'Time', 'home_team', 'Referee', 'away_team', 'home_coef', 'draw_coef',
       'away_coef']

In [ ]:
def iter_over_dataset(df: pd.DataFrame):
    columns_known_before_match = ['Division', 'Time', 'home_team', 'Referee', 'away_team', 'home_coef', 'draw_coef',
       'away_coef']
    for _, row in df.iterrows():
        yield True, row[columns_known_before_match] # is before match, information 
        yield False, row

In [ ]:
def get_team_stat(teams_stat: tp.Dict[int, tp.List], team_id, n_matches):
    if team_id in teams_stat:
        return np.nanmean(teams_stat[team_id][-n_matches:])
    else:
        return 0

In [ ]:
stat_dict = {}

In [ ]:
def calculate_last_matches_stat(df: pd.DataFrame, stat, n_matches=5):
    teams_stat: tp.Dict[int, tp.List] = dict()
    iterator = iter_over_dataset(df)
    for match_not_happened, row in iterator:
        if match_not_happened:
            home_team_stat = get_team_stat(teams_stat, row['home_team'], n_matches)
            away_team_stat = get_team_stat(teams_stat, row['away_team'], n_matches)
            yield home_team_stat, away_team_stat
        else:
            if row['home_team'] in teams_stat:
                teams_stat[row['home_team']].append(row['home_' + stat])
            else:
                teams_stat[row['home_team']] = [row['home_' + stat]]

            if row['away_team'] in teams_stat:
                teams_stat[row['away_team']].append(row['away_' + stat])
            else:
                teams_stat[row['away_team']] = [row['away_' + stat]]
    global stat_dict
    stat_dict[stat] = teams_stat

In [ ]:
for row in calculate_last_matches_stat(stat_df.iloc[:20], 'full_time_goals', 2):
    print(row)

(0, 0)
(0, 0)
(0, 0)
(0, 0)
(0, 0)
(0, 0)
(0, 0)
(0, 0)
(0, 0)
(0, 0)
(0, 0)
(0, 0)
(0, 0)
(0, 0)
(0, 0)
(0.0, 1.0)
(2.0, 0.0)
(4.0, 3.0)
(0, 0)
(0.0, 2.0)


In [ ]:
stat_df.iloc[:20]

Unnamed: 0  Division  Time  ...  home_coef  draw_coef  away_coef
0            0         0   NaN  ...   3.627690   3.577721   2.198600
1            1         0   NaN  ...   1.608321   4.251999   6.533805
2            2         0   NaN  ...   2.166811   3.486596   3.821467
3            3         0   NaN  ...   2.259244   3.592401   3.460103
4            4         1   NaN  ...   2.424278   3.414191   3.282876
5            5         1   NaN  ...   2.787163   3.375001   2.817568
6            6         1   NaN  ...   2.080239   3.582070   3.998117
7            7         1   NaN  ...   2.099892   3.449822   4.099789
8            8         1   NaN  ...   1.312957   5.807312  13.129574
9            9         0   NaN  ...   1.528475   4.476952   7.553624
10          10         0   NaN  ...   2.597933   3.359046   3.054601
11          11         0   NaN  ...   1.709009   3.960881   5.800579
12          12         0   NaN  ...   2.289645   3.454378   3.524063
13          13         1   NaN  ...   1.714712   4.034617   5.587944
14          14         0   NaN  ...   1.816078   3.824924   5.052552
15          15         0   NaN  ...   1.603522   4.325550   6.443783
16          16         0   NaN  ...   1.888972   3.767844   4.646670
17          17         0   NaN  ...   3.302800   3.565408   2.343271
18          18         2   NaN  ...   2.713707   3.738885   2.673504
19          19         1   NaN  ...   2.717966   3.336607   2.920799

[20 rows x 25 columns]

In [ ]:
cols = ['full_time_goals', 'half_time_goals', 'shots', 'shots_on_target', 
        'fouls', 'corners', 'yellow_cards', 'red_cards']
for stat in cols:
    for n_matches in range(1, 10, 3):
        print(n_matches)
        stats = []
        for row in calculate_last_matches_stat(stat_df, stat, n_matches):
            stats.append(row)
        df = pd.DataFrame(stats, columns=['home_mean_' + stat + f'_{n_matches}', 'away_mean_' + stat + f'_{n_matches}'])
        stat_df = stat_df.merge(df, left_index=True, right_index=True)

1
4
7
1
4
7
1


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:3: RuntimeWarning: Mean of empty slice
  This is separate from the ipykernel package so we can avoid doing imports until


4
7
1
4
7
1
4
7
1
4
7
1
4
7
1
4
7


In [ ]:
stat_df = stat_df.assign(outcome = lambda df: 1 * (df.home_full_time_goals > df.away_full_time_goals) -
                         1 * (df.home_full_time_goals < df.away_full_time_goals))

In [ ]:
stat_df

Unnamed: 0  Division  ...  away_mean_red_cards_7  outcome
0               0         0  ...               0.000000        0
1               1         0  ...               0.000000        0
2               2         0  ...               0.000000        0
3               3         0  ...               0.000000        1
4               4         1  ...               0.000000        0
...           ...       ...  ...                    ...      ...
39987       39995        15  ...               0.000000       -1
39988       39996        15  ...               0.000000        1
39989       39997        15  ...               0.142857       -1
39990       39998        13  ...               0.000000        0
39991       39999         6  ...               0.285714        0

[39992 rows x 74 columns]

In [ ]:
stat_df.to_csv('stat_df_features.csv')

In [ ]:
import json

with open('stat_dict.json', 'w') as fp:
    json.dump(stat_dict, fp)